# Baseball - Predicting players' salary

In this notebook, we will benchmark several of getML's feature learning algorithms against featuretools using a dataset related to baseball players' salary.

Summary:

- Prediction type: __Regression model__
- Domain: __Sports__
- Prediction target: __Salaries__ 
- Population size: __23111__

## Background

In the late 1990s, the Oakland Athletics began focusing on the idea of *sabermetrics*, using statistical methods to identify undervalued baseball players. This was done to compensate for the fact that the team had a significantly smaller budget than most other teams in its league. Under its general manager Billy Beane, the Oakland Athletics became the first team in over 100 years to win 20 consecutive games in a row, despite still being significantly disadvantaged in terms of its budget. After this remarkable success, the use of sabermetrics quickly became the norm in baseball. These events have been documented in a bestselling book and a movie, both called *Moneyball*. 

In this notebook, we will demonstrate that relational learning can be used for sabermetrics. Specifically, we will develop a model to predict players' salary using getML's statistical relational learning algorithms. Such predictions can then be used to identify undervalued players. 

The dataset has been downloaded from the [CTU Prague relational learning repository](https://relational.fit.cvut.cz/dataset/Lahman) (Motl and Schulte, 2015) (Now residing at [relational-data.org](https://relational-data.org/dataset/Lahman).).

We will benchmark [getML](https://www.getml.com) 's feature learning algorithms against [featuretools](https://www.featuretools.com), an open-source implementation of the propositionalization algorithm, similar to getML's FastProp.

## Analysis

In [2]:
!pip install -q "getml==1.5.0" "pandas~=2.2" "featuretools==1.31.0" 

Let's get started with the analysis and set up your session:

In [75]:
import os
os.environ["PYARROW_IGNORE_TIMEZONE"] = "1"
from pathlib import Path
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
import numpy as np
import pandas as pd 

import featuretools
import woodwork as ww
import getml

getml.engine.launch(home_directory=Path.home(), allow_remote_ips=True, token='token')
getml.engine.set_project('baseball')

Launching ./getML --allow-push-notifications=true --allow-remote-ips=true --home-directory=/home/getml --in-memory=true --install=false --launch-browser=true --log=false --token=token in /home/getml/.getML/getml-1.5.0-x64-linux...
Launched the getML Engine. The log output will be stored in /home/getml/.getML/logs/20240903152037.log.
  Loading pipelines... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:005m 66% • 00:01


Connected to project 'baseball'

### 1. Loading data

#### 1.1 Download from source

We begin by downloading the data:

In [5]:
conn = getml.database.connect_mysql(
    host="db.relational-data.org",
    dbname="lahman_2014",
    port=3306,
    user="guest",
    password="relational"
)

conn

Connection(dbname='lahman_2014',
           dialect='mysql',
           host='db.relational-data.org',
           port=3306)

In [6]:
def load_if_needed(name):
    """
    Loads the data from the relational learning
    repository, if the data frame has not already
    been loaded.
    """
    if not getml.data.exists(name):
        data_frame = getml.data.DataFrame.from_db(
            name=name,
            table_name=name,
            conn=conn
        )
        data_frame.save()
    else:
        data_frame = getml.data.load_data_frame(name)
    return data_frame

In [7]:
allstarfull = load_if_needed("allstarfull")
awardsplayers = load_if_needed("awardsplayers")
awardsshareplayers = load_if_needed("awardsshareplayers")
batting = load_if_needed("batting")
battingpost = load_if_needed("battingpost")
fielding = load_if_needed("fielding")
fieldingpost = load_if_needed("fieldingpost")
pitching = load_if_needed("pitching")
pitchingpost = load_if_needed("pitchingpost")
salaries = load_if_needed("salaries")

In [8]:
allstarfull

name         yearID        gameNum             GP    startingPos   playerID        gameID          teamID       
role   unused_float   unused_float   unused_float   unused_float   unused_string   unused_string   unused_string
   0           1955              0              1           nan    aaronha01       NLS195507120    ML1          
   1           1956              0              1           nan    aaronha01       ALS195607100    ML1          
   2           1957              0              1             9    aaronha01       NLS195707090    ML1          
   3           1958              0              1             9    aaronha01       ALS195807080    ML1          
   4           1959              1              1             9    aaronha01       NLS195907070    ML1          
                ...            ...            ...            ...   ...             ...             ...          
4826           1978              0              1             9    ziskri01        NLS197807110    TEX          
4827           2002              0              1           nan    zitoba01        NLS200207090    OAK          
4828           2003              0              0           nan    zitoba01        ALS200307150    OAK          
4829           2006              0              1           nan    zitoba01        NLS200607110    OAK          
4830           2009              0              1           nan    zobribe01       NLS200907140    TBA          

name   lgID         
role   unused_string
   0   NL           
   1   NL           
   2   NL           
   3   NL           
   4   NL           
       ...          
4826   AL           
4827   AL           
4828   AL           
4829   AL           
4830   AL           


4831 rows x 8 columns
memory usage: 0.45 MB
type: getml.DataFrame

In [9]:
awardsplayers

name         yearID   playerID        awardID                            lgID            tie             notes        
role   unused_float   unused_string   unused_string                      unused_string   unused_string   unused_string
   0           1877   bondto01        Pitching Triple Crown              NL              NULL            NULL         
   1           1878   hinespa01       Triple Crown                       NL              NULL            NULL         
   2           1884   heckegu01       Pitching Triple Crown              AA              NULL            NULL         
   3           1884   radboch01       Pitching Triple Crown              NL              NULL            NULL         
   4           1887   oneilti01       Triple Crown                       AA              NULL            NULL         
                ...   ...             ...                                ...             ...             ...          
5790           2012   larocad01       Silver Slugger                     NL              NULL            1B           
5791           2012   cabremi01       Triple Crown                       NL              NULL            NULL         
5792           2012   cabremi01       TSN Major League Player of the Y...   ML              NULL            NULL         
5793           2012   verlaju01       TSN Pitcher of the Year            AL              Y               NULL         
5794           2012   dickera01       TSN Pitcher of the Year            NL              NULL            NULL         


5795 rows x 6 columns
memory usage: 0.48 MB
type: getml.DataFrame

In [10]:
awardsshareplayers

name         yearID      pointsWon      pointsMax     votesFirst   awardID              lgID            playerID     
role   unused_float   unused_float   unused_float   unused_float   unused_string        unused_string   unused_string
   0           1956              1             16              1   Cy Young             ML              fordwh01     
   1           1956              4             16              4   Cy Young             ML              maglisa01    
   2           1956             10             16             10   Cy Young             ML              newcodo01    
   3           1956              1             16              1   Cy Young             ML              spahnwa01    
   4           1957              1             16              1   Cy Young             ML              donovdi01    
                ...            ...            ...            ...   ...                  ...             ...          
6284           2006              1            160              0   Rookie of the Year   NL              willijo03    
6285           2006            101            160             10   Rookie of the Year   NL              zimmery01    
6286           2008              3            140              0   Rookie of the Year   AL              devinjo01    
6287           2008            158            160             31   Rookie of the Year   NL              sotoge01     
6288           2008              9            160              0   Rookie of the Year   NL              volqued01    


6289 rows x 7 columns
memory usage: 0.47 MB
type: getml.DataFrame

In [11]:
batting

name         yearID          stint              G      G_batting   ...           GIDP          G_old   playerID     
 role   unused_float   unused_float   unused_float   unused_float   ...   unused_float   unused_float   unused_string
    0           2004              1             11             11   ...             0             11    aardsda01    
    1           2006              1             45             43   ...             0             45    aardsda01    
    2           2007              1             25              2   ...             0              2    aardsda01    
    3           2008              1             47              5   ...             0              5    aardsda01    
    4           2009              1             73              3   ...             0            nan    aardsda01    
                 ...            ...            ...            ...                  ...            ...   ...          
92348           1959              1              6              6   ...             0              6    zuverge01    
92349           1910              1             27             27   ...           nan             27    zwilldu01    
92350           1914              1            154            154   ...           nan            154    zwilldu01    
92351           1915              1            150            150   ...           nan            150    zwilldu01    
92352           1916              1             35             35   ...           nan             35    zwilldu01    

 name   teamID          lgID         
 role   unused_string   unused_string
    0   SFN             NL           
    1   CHN             NL           
    2   CHA             AL           
    3   BOS             AL           
    4   SEA             AL           
        ...             ...          
92348   BAL             AL           
92349   CHA             AL           
92350   CHF             FL           
92351   CHF             FL           
92352   CHN             NL           


92353 rows x 24 columns
memory usage: 19.29 MB
type: getml.DataFrame

In [12]:
battingpost

name         yearID              G             AB              R   ...           GIDP   round           playerID     
role   unused_float   unused_float   unused_float   unused_float   ...   unused_float   unused_string   unused_string
   0           1884              1              2              0   ...           nan    WS              becanbu01    
   1           1884              3             10              1   ...           nan    WS              bradyst01    
   2           1884              3             10              2   ...           nan    WS              carrocl01    
   3           1884              3              9              3   ...           nan    WS              dennyje01    
   4           1884              3             10              0   ...           nan    WS              esterdu01    
                ...            ...            ...            ...                  ...   ...             ...          
9793           2012              2              5              1   ...           nan    WS              theriry01    
9794           2012              1              0              0   ...           nan    WS              valvejo01    
9795           2012              1              1              0   ...           nan    WS              verlaju01    
9796           2012              1              0              0   ...           nan    WS              vogelry01    
9797           2012              1              2              0   ...           nan    WS              zitoba01     

name   teamID          lgID         
role   unused_string   unused_string
   0   NY4             AA           
   1   NY4             AA           
   2   PRO             NL           
   3   PRO             NL           
   4   NY4             AA           
       ...             ...          
9793   SFN             NL           
9794   DET             AL           
9795   DET             AL           
9796   SFN             NL           
9797   SFN             NL           


9798 rows x 22 columns
memory usage: 1.93 MB
type: getml.DataFrame

In [13]:
fielding

name         yearID          stint              G             GS   ...             ZR   playerID        teamID       
  role   unused_float   unused_float   unused_float   unused_float   ...   unused_float   unused_string   unused_string
     0           2004              1             11             0    ...           nan    aardsda01       SFN          
     1           2006              1             45             0    ...           nan    aardsda01       CHN          
     2           2007              1             25             0    ...           nan    aardsda01       CHA          
     3           2008              1             47             0    ...           nan    aardsda01       BOS          
     4           2009              1             73             0    ...           nan    aardsda01       SEA          
                  ...            ...            ...            ...                  ...   ...             ...          
137970           1910              1             27           nan    ...           nan    zwilldu01       CHA          
137971           1914              1            154           nan    ...           nan    zwilldu01       CHF          
137972           1915              1              3           nan    ...           nan    zwilldu01       CHF          
137973           1915              1            148           nan    ...           nan    zwilldu01       CHF          
137974           1916              1             10           nan    ...           nan    zwilldu01       CHN          

  name   lgID            POS          
  role   unused_string   unused_string
     0   NL              P            
     1   NL              P            
     2   AL              P            
     3   AL              P            
     4   AL              P            
         ...             ...          
137970   AL              OF           
137971   FL              OF           
137972   FL              1B           
137973   FL              OF           
137974   NL              OF           


137975 rows x 18 columns
memory usage: 22.57 MB
type: getml.DataFrame

In [14]:
fieldingpost

name         yearID              G             GS        InnOuts   ...   playerID        teamID          lgID         
 role   unused_float   unused_float   unused_float   unused_float   ...   unused_string   unused_string   unused_string
    0           1957              7              7            186   ...   aaronha01       ML1             NL           
    1           1958              1              1             21   ...   aaronha01       ML1             NL           
    2           1958              7              6            168   ...   aaronha01       ML1             NL           
    3           1969              3              3             78   ...   aaronha01       ATL             NL           
    4           1979              2              0             15   ...   aasedo01        CAL             AL           
                 ...            ...            ...            ...         ...             ...             ...          
10341           2006              1              1             24   ...   zitoba01        OAK             AL           
10342           2012              1              1             23   ...   zitoba01        SFN             NL           
10343           2012              1              1              8   ...   zitoba01        SFN             NL           
10344           2012              1              1             17   ...   zitoba01        SFN             NL           
10345           1946              1              0              6   ...   zuberbi01       BOS             AL           

 name   round           POS          
 role   unused_string   unused_string
    0   WS              CF           
    1   WS              CF           
    2   WS              RF           
    3   NLCS            RF           
    4   ALCS            P            
        ...             ...          
10341   ALDS2           P            
10342   NLCS            P            
10343   NLDS2           P            
10344   WS              P            
10345   WS              P            


10346 rows x 17 columns
memory usage: 1.65 MB
type: getml.DataFrame

In [15]:
pitching

name         yearID          stint              W              L   ...             SF           GIDP   playerID     
 role   unused_float   unused_float   unused_float   unused_float   ...   unused_float   unused_float   unused_string
    0           2004              1              1              0   ...           nan            nan    aardsda01    
    1           2006              1              3              0   ...           nan            nan    aardsda01    
    2           2007              1              2              1   ...           nan            nan    aardsda01    
    3           2008              1              4              2   ...           nan            nan    aardsda01    
    4           2009              1              3              6   ...           nan            nan    aardsda01    
                 ...            ...            ...            ...                  ...            ...   ...          
39356           1955              2              4              3   ...           nan            nan    zuverge01    
39357           1956              1              7              6   ...           nan            nan    zuverge01    
39358           1957              1             10              6   ...           nan            nan    zuverge01    
39359           1958              1              2              2   ...           nan            nan    zuverge01    
39360           1959              1              0              1   ...           nan            nan    zuverge01    

 name   teamID          lgID         
 role   unused_string   unused_string
    0   SFN             NL           
    1   CHN             NL           
    2   CHA             AL           
    3   BOS             AL           
    4   SEA             AL           
        ...             ...          
39356   BAL             AL           
39357   BAL             AL           
39358   BAL             AL           
39359   BAL             AL           
39360   BAL             AL           


39361 rows x 30 columns
memory usage: 10.11 MB
type: getml.DataFrame

In [16]:
pitchingpost

name         yearID              W              L              G   ...           GIDP   playerID        round        
role   unused_float   unused_float   unused_float   unused_float   ...   unused_float   unused_string   unused_string
   0           1979              1              0              2   ...              0   aasedo01        ALCS         
   1           1975              0              0              1   ...              0   abbotgl01       ALCS         
   2           2000              0              1              1   ...              0   abbotpa01       ALCS         
   3           2000              1              0              1   ...              1   abbotpa01       ALDS2        
   4           2001              0              0              1   ...              0   abbotpa01       ALCS         
                ...            ...            ...            ...                  ...   ...             ...          
4192           2006              1              0              1   ...              0   zitoba01        ALDS2        
4193           2012              1              0              1   ...              1   zitoba01        NLCS         
4194           2012              0              0              1   ...              0   zitoba01        NLDS2        
4195           2012              1              0              1   ...              1   zitoba01        WS           
4196           1946              0              0              1   ...              1   zuberbi01       WS           

name   teamID          lgID         
role   unused_string   unused_string
   0   CAL             AL           
   1   OAK             AL           
   2   SEA             AL           
   3   SEA             AL           
   4   SEA             AL           
       ...             ...          
4192   OAK             AL           
4193   SFN             NL           
4194   SFN             NL           
4195   SFN             NL           
4196   BOS             AL           


4197 rows x 30 columns
memory usage: 1.10 MB
type: getml.DataFrame

In [17]:
salaries

name         yearID         salary   teamID          lgID            playerID     
 role   unused_float   unused_float   unused_string   unused_string   unused_string
    0           1985         870000   ATL             NL              barkele01    
    1           1985         550000   ATL             NL              bedrost01    
    2           1985         545000   ATL             NL              benedbr01    
    3           1985         633333   ATL             NL              campri01     
    4           1985         625000   ATL             NL              ceronri01    
                 ...            ...   ...             ...             ...          
23106           2012         750000   WAS             NL              tracych01    
23107           2012        4000000   WAS             NL              wangch01     
23108           2012       13571428   WAS             NL              werthja01    
23109           2012        2300000   WAS             NL              zimmejo02    
23110           2012       12000000   WAS             NL              zimmery01    


23111 rows x 5 columns
memory usage: 1.31 MB
type: getml.DataFrame

#### 1.2 Prepare data for getML

getML requires that we define *roles* for each of the columns.

In [18]:
allstarfull["year"] = allstarfull["yearID"].as_str().as_ts(["%Y"])

allstarfull.set_role(["playerID"], getml.data.roles.join_key)
allstarfull.set_role(allstarfull.roles.unused_string, getml.data.roles.categorical)
allstarfull.set_role(allstarfull.roles.unused_float, getml.data.roles.numerical)
allstarfull.set_role("year", getml.data.roles.time_stamp)

allstarfull.set_role("yearID", getml.data.roles.unused_float)

allstarfull

name                          year    playerID   gameID         teamID        lgID            gameNum          GP
role                    time_stamp    join_key   categorical    categorical   categorical   numerical   numerical
unit   time stamp, comparison only                                                                               
   0                    1955-01-01   aaronha01   NLS195507120   ML1           NL                    0           1
   1                    1956-01-01   aaronha01   ALS195607100   ML1           NL                    0           1
   2                    1957-01-01   aaronha01   NLS195707090   ML1           NL                    0           1
   3                    1958-01-01   aaronha01   ALS195807080   ML1           NL                    0           1
   4                    1959-01-01   aaronha01   NLS195907070   ML1           NL                    1           1
                               ...         ...   ...            ...           ...                 ...         ...
4826                    1978-01-01    ziskri01   NLS197807110   TEX           AL                    0           1
4827                    2002-01-01    zitoba01   NLS200207090   OAK           AL                    0           1
4828                    2003-01-01    zitoba01   ALS200307150   OAK           AL                    0           0
4829                    2006-01-01    zitoba01   NLS200607110   OAK           AL                    0           1
4830                    2009-01-01   zobribe01   NLS200907140   TBA           AL                    0           1

name   startingPos         yearID
role     numerical   unused_float
unit                             
   0          nan            1955
   1          nan            1956
   2            9            1957
   3            9            1958
   4            9            1959
               ...            ...
4826            9            1978
4827          nan            2002
4828          nan            2003
4829          nan            2006
4830          nan            2009


4831 rows x 9 columns
memory usage: 0.27 MB
type: getml.DataFrame

In [19]:
awardsplayers["year"] = awardsplayers["yearID"].as_str().as_ts(["%Y"])

awardsplayers.set_role(["playerID"], getml.data.roles.join_key)
awardsplayers.set_role(["awardID", "lgID", "notes"], getml.data.roles.categorical)
awardsplayers.set_role("year", getml.data.roles.time_stamp)

awardsplayers

name                          year    playerID   awardID                            lgID          notes               yearID
role                    time_stamp    join_key   categorical                        categorical   categorical   unused_float
unit   time stamp, comparison only                                                                                          
   0                    1877-01-01    bondto01   Pitching Triple Crown              NL            NULL                  1877
   1                    1878-01-01   hinespa01   Triple Crown                       NL            NULL                  1878
   2                    1884-01-01   heckegu01   Pitching Triple Crown              AA            NULL                  1884
   3                    1884-01-01   radboch01   Pitching Triple Crown              NL            NULL                  1884
   4                    1887-01-01   oneilti01   Triple Crown                       AA            NULL                  1887
                               ...         ...   ...                                ...           ...                    ...
5790                    2012-01-01   larocad01   Silver Slugger                     NL            1B                    2012
5791                    2012-01-01   cabremi01   Triple Crown                       NL            NULL                  2012
5792                    2012-01-01   cabremi01   TSN Major League Player of the Y...   ML            NULL       
5793                    2012-01-01   verlaju01   TSN Pitcher of the Year            AL            NULL                  2012
5794                    2012-01-01   dickera01   TSN Pitcher of the Year            NL            NULL                  2012

name   tie          
role   unused_string
unit                
   0   NULL         
   1   NULL         
   2   NULL         
   3   NULL         
   4   NULL         
       ...          
5790   NULL         
5791   NULL         
5792           2012   NULL         
5793   Y            
5794   NULL         


5795 rows x 7 columns
memory usage: 0.24 MB
type: getml.DataFrame

In [20]:
awardsshareplayers["year"] = awardsshareplayers["yearID"].as_str().as_ts(["%Y"])

awardsshareplayers.set_role(["playerID"], getml.data.roles.join_key)
awardsshareplayers.set_role(awardsshareplayers.roles.unused_float, getml.data.roles.numerical)
awardsshareplayers.set_role(awardsshareplayers.roles.unused_string, getml.data.roles.categorical)
awardsshareplayers.set_role("yearID", getml.data.roles.unused_float)
awardsshareplayers.set_role("year", getml.data.roles.time_stamp)

awardsshareplayers

name                          year    playerID   awardID              lgID          pointsWon   pointsMax   votesFirst
role                    time_stamp    join_key   categorical          categorical   numerical   numerical    numerical
unit   time stamp, comparison only                                                                                    
   0                    1956-01-01    fordwh01   Cy Young             ML                    1          16            1
   1                    1956-01-01   maglisa01   Cy Young             ML                    4          16            4
   2                    1956-01-01   newcodo01   Cy Young             ML                   10          16           10
   3                    1956-01-01   spahnwa01   Cy Young             ML                    1          16            1
   4                    1957-01-01   donovdi01   Cy Young             ML                    1          16            1
                               ...         ...   ...                  ...                 ...         ...          ...
6284                    2006-01-01   willijo03   Rookie of the Year   NL                    1         160            0
6285                    2006-01-01   zimmery01   Rookie of the Year   NL                  101         160           10
6286                    2008-01-01   devinjo01   Rookie of the Year   AL                    3         140            0
6287                    2008-01-01    sotoge01   Rookie of the Year   NL                  158         160           31
6288                    2008-01-01   volqued01   Rookie of the Year   NL                    9         160            0

name         yearID
role   unused_float
unit               
   0           1956
   1           1956
   2           1956
   3           1956
   4           1957
                ...
6284           2006
6285           2006
6286           2008
6287           2008
6288           2008


6289 rows x 8 columns
memory usage: 0.33 MB
type: getml.DataFrame

In [21]:
batting["year"] = batting["yearID"].as_str().as_ts(["%Y"])

batting.set_role(["playerID", "teamID"], getml.data.roles.join_key)
batting.set_role(batting.roles.unused_float, getml.data.roles.numerical)
batting.set_role(batting.roles.unused_string, getml.data.roles.categorical)
batting.set_role("yearID", getml.data.roles.unused_float)
batting.set_role("year", getml.data.roles.time_stamp)

batting

name                          year    playerID     teamID   lgID          ...          SH          SF        GIDP       G_old
 role                    time_stamp    join_key   join_key   categorical   ...   numerical   numerical   numerical   numerical
 unit   time stamp, comparison only                                        ...                                                
    0                    2004-01-01   aardsda01        SFN   NL            ...           0          0           0          11 
    1                    2006-01-01   aardsda01        CHN   NL            ...           1          0           0          45 
    2                    2007-01-01   aardsda01        CHA   AL            ...           0          0           0           2 
    3                    2008-01-01   aardsda01        BOS   AL            ...           0          0           0           5 
    4                    2009-01-01   aardsda01        SEA   AL            ...           0          0           0         nan 
                                ...         ...        ...   ...                       ...         ...         ...         ...
92348                    1959-01-01   zuverge01        BAL   AL            ...           0          0           0           6 
92349                    1910-01-01   zwilldu01        CHA   AL            ...           1        nan         nan          27 
92350                    1914-01-01   zwilldu01        CHF   FL            ...          10        nan         nan         154 
92351                    1915-01-01   zwilldu01        CHF   FL            ...          18        nan         nan         150 
92352                    1916-01-01   zwilldu01        CHN   NL            ...           2        nan         nan          35 

 name         yearID
 role   unused_float
 unit               
    0           2004
    1           2006
    2           2007
    3           2008
    4           2009
                 ...
92348           1959
92349           1910
92350           1914
92351           1915
92352           1916


92353 rows x 25 columns
memory usage: 17.36 MB
type: getml.DataFrame

In [22]:
battingpost["year"] = battingpost["yearID"].as_str().as_ts(["%Y"])

battingpost.set_role(["playerID", "teamID"], getml.data.roles.join_key)
battingpost.set_role(battingpost.roles.unused_float, getml.data.roles.numerical)
battingpost.set_role(battingpost.roles.unused_string, getml.data.roles.categorical)
battingpost.set_role("yearID", getml.data.roles.unused_float)
battingpost.set_role("year", getml.data.roles.time_stamp)

battingpost

name                          year    playerID     teamID   round         ...         HBP          SH          SF        GIDP
role                    time_stamp    join_key   join_key   categorical   ...   numerical   numerical   numerical   numerical
unit   time stamp, comparison only                                        ...                                                
   0                    1884-01-01   becanbu01        NY4   WS            ...        nan         nan         nan         nan 
   1                    1884-01-01   bradyst01        NY4   WS            ...        nan         nan         nan         nan 
   2                    1884-01-01   carrocl01        PRO   WS            ...        nan         nan         nan         nan 
   3                    1884-01-01   dennyje01        PRO   WS            ...        nan         nan         nan         nan 
   4                    1884-01-01   esterdu01        NY4   WS            ...        nan         nan         nan         nan 
                               ...         ...        ...   ...                       ...         ...         ...         ...
9793                    2012-01-01   theriry01        SFN   WS            ...        nan         nan         nan         nan 
9794                    2012-01-01   valvejo01        DET   WS            ...        nan         nan         nan         nan 
9795                    2012-01-01   verlaju01        DET   WS            ...        nan         nan         nan         nan 
9796                    2012-01-01   vogelry01        SFN   WS            ...        nan         nan         nan         nan 
9797                    2012-01-01    zitoba01        SFN   WS            ...        nan         nan         nan         nan 

name         yearID
role   unused_float
unit               
   0           1884
   1           1884
   2           1884
   3           1884
   4           1884
                ...
9793           2012
9794           2012
9795           2012
9796           2012
9797           2012


9798 rows x 23 columns
memory usage: 1.65 MB
type: getml.DataFrame

In [23]:
fielding["year"] = fielding["yearID"].as_str().as_ts(["%Y"])

fielding.set_role(["playerID", "teamID"], getml.data.roles.join_key)
fielding.set_role(["stint", "G","GS","InnOuts", "PO", "A", "E", "DP"], getml.data.roles.numerical)
fielding.set_role(fielding.roles.unused_string, getml.data.roles.categorical)
fielding.set_role("year", getml.data.roles.time_stamp)

fielding

name                          year    playerID     teamID   lgID          ...             PB             WP             SB
  role                    time_stamp    join_key   join_key   categorical   ...   unused_float   unused_float   unused_float
  unit   time stamp, comparison only                                        ...                                             
     0                    2004-01-01   aardsda01        SFN   NL            ...           nan            nan            nan 
     1                    2006-01-01   aardsda01        CHN   NL            ...           nan            nan            nan 
     2                    2007-01-01   aardsda01        CHA   AL            ...           nan            nan            nan 
     3                    2008-01-01   aardsda01        BOS   AL            ...           nan            nan            nan 
     4                    2009-01-01   aardsda01        SEA   AL            ...             0            nan              0 
                                 ...         ...        ...   ...                          ...            ...            ...
137970                    1910-01-01   zwilldu01        CHA   AL            ...           nan            nan            nan 
137971                    1914-01-01   zwilldu01        CHF   FL            ...           nan            nan            nan 
137972                    1915-01-01   zwilldu01        CHF   FL            ...           nan            nan            nan 
137973                    1915-01-01   zwilldu01        CHF   FL            ...           nan            nan            nan 
137974                    1916-01-01   zwilldu01        CHN   NL            ...           nan            nan            nan 

  name             CS             ZR
  role   unused_float   unused_float
  unit                              
     0           nan            nan 
     1           nan            nan 
     2           nan            nan 
     3           nan            nan 
     4             0            nan 
                  ...            ...
137970           nan            nan 
137971           nan            nan 
137972           nan            nan 
137973           nan            nan 
137974           nan            nan 


137975 rows x 19 columns
memory usage: 18.76 MB
type: getml.DataFrame

In [24]:
fieldingpost["year"] = fieldingpost["yearID"].as_str().as_ts(["%Y"])

fieldingpost.set_role(["playerID", "teamID"], getml.data.roles.join_key)
fieldingpost.set_role(["G", "GS", "InnOuts", "PO", "A", "E", "DP", "TP", "SB", "CS"], getml.data.roles.numerical)
fieldingpost.set_role(fieldingpost.roles.unused_string, getml.data.roles.categorical)
fieldingpost.set_role("year", getml.data.roles.time_stamp)

fieldingpost

name                          year    playerID     teamID   lgID          ...          TP          SB          CS
 role                    time_stamp    join_key   join_key   categorical   ...   numerical   numerical   numerical
 unit   time stamp, comparison only                                        ...                                    
    0                    1957-01-01   aaronha01        ML1   NL            ...           0        nan         nan 
    1                    1958-01-01   aaronha01        ML1   NL            ...           0        nan         nan 
    2                    1958-01-01   aaronha01        ML1   NL            ...           0        nan         nan 
    3                    1969-01-01   aaronha01        ATL   NL            ...           0        nan         nan 
    4                    1979-01-01    aasedo01        CAL   AL            ...           0          0           0 
                                ...         ...        ...   ...                       ...         ...         ...
10341                    2006-01-01    zitoba01        OAK   AL            ...           0          0           1 
10342                    2012-01-01    zitoba01        SFN   NL            ...           0          0           0 
10343                    2012-01-01    zitoba01        SFN   NL            ...           0          0           0 
10344                    2012-01-01    zitoba01        SFN   NL            ...           0          0           0 
10345                    1946-01-01   zuberbi01        BOS   AL            ...           0          0           0 

 name         yearID             PB
 role   unused_float   unused_float
 unit                              
    0           1957           nan 
    1           1958           nan 
    2           1958           nan 
    3           1969           nan 
    4           1979           nan 
                 ...            ...
10341           2006           nan 
10342           2012             0 
10343           2012             0 
10344           2012             0 
10345           1946           nan 


10346 rows x 18 columns
memory usage: 1.28 MB
type: getml.DataFrame

In [25]:
pitching["year"] = pitching["yearID"].as_str().as_ts(["%Y"])

pitching.set_role(["playerID", "teamID"], getml.data.roles.join_key)
pitching.set_role([
    "stint", 
    "W", 
    "L", 
    "G", 
    "GS", 
    "CG", 
    "SHO", 
    "SV", 
    "IPouts", 
    "H", 
    "ER", 
    "HR", 
    "BB", 
    "SO", 
    "BAOpp", 
    "ERA", 
    "IBB", 
    "WP", 
    "HBP", 
    "BK", 
    "BFP", 
    "GF", 
    "R"], getml.data.roles.numerical)
pitching.set_role(pitching.roles.unused_string, getml.data.roles.categorical)
pitching.set_role("yearID", getml.data.roles.unused_float)
pitching.set_role("year", getml.data.roles.time_stamp)

pitching

name                          year    playerID     teamID   lgID          ...           R         yearID             SH
 role                    time_stamp    join_key   join_key   categorical   ...   numerical   unused_float   unused_float
 unit   time stamp, comparison only                                        ...                                          
    0                    2004-01-01   aardsda01        SFN   NL            ...           8           2004           nan 
    1                    2006-01-01   aardsda01        CHN   NL            ...          25           2006           nan 
    2                    2007-01-01   aardsda01        CHA   AL            ...          24           2007           nan 
    3                    2008-01-01   aardsda01        BOS   AL            ...          32           2008           nan 
    4                    2009-01-01   aardsda01        SEA   AL            ...          23           2009           nan 
                                ...         ...        ...   ...                       ...            ...            ...
39356                    1955-01-01   zuverge01        BAL   AL            ...          28           1955           nan 
39357                    1956-01-01   zuverge01        BAL   AL            ...          52           1956           nan 
39358                    1957-01-01   zuverge01        BAL   AL            ...          37           1957           nan 
39359                    1958-01-01   zuverge01        BAL   AL            ...          29           1958           nan 
39360                    1959-01-01   zuverge01        BAL   AL            ...           7           1959           nan 

 name             SF           GIDP
 role   unused_float   unused_float
 unit                              
    0           nan            nan 
    1           nan            nan 
    2           nan            nan 
    3           nan            nan 
    4           nan            nan 
                 ...            ...
39356           nan            nan 
39357           nan            nan 
39358           nan            nan 
39359           nan            nan 
39360           nan            nan 


39361 rows x 31 columns
memory usage: 9.29 MB
type: getml.DataFrame

In [26]:
pitchingpost["year"] = pitchingpost["yearID"].as_str().as_ts(["%Y"])

pitchingpost.set_role(["playerID", "teamID"], getml.data.roles.join_key)
pitchingpost.set_role(pitchingpost.roles.unused_float, getml.data.roles.numerical)
pitchingpost.set_role(pitchingpost.roles.unused_string, getml.data.roles.categorical)
pitchingpost.set_role("yearID", getml.data.roles.unused_float)
pitchingpost.set_role("year", getml.data.roles.time_stamp)

pitchingpost

name                          year    playerID     teamID   round         ...           R          SH          SF        GIDP
role                    time_stamp    join_key   join_key   categorical   ...   numerical   numerical   numerical   numerical
unit   time stamp, comparison only                                        ...                                                
   0                    1979-01-01    aasedo01        CAL   ALCS          ...           1          0           1            0
   1                    1975-01-01   abbotgl01        OAK   ALCS          ...           0          0           0            0
   2                    2000-01-01   abbotpa01        SEA   ALCS          ...           3          0           0            0
   3                    2000-01-01   abbotpa01        SEA   ALDS2         ...           2          0           1            1
   4                    2001-01-01   abbotpa01        SEA   ALCS          ...           0          1           0            0
                               ...         ...        ...   ...                       ...         ...         ...         ...
4192                    2006-01-01    zitoba01        OAK   ALDS2         ...           1          1           0            0
4193                    2012-01-01    zitoba01        SFN   NLCS          ...           0        nan         nan            1
4194                    2012-01-01    zitoba01        SFN   NLDS2         ...           2        nan         nan            0
4195                    2012-01-01    zitoba01        SFN   WS            ...           1        nan         nan            1
4196                    1946-01-01   zuberbi01        BOS   WS            ...           1          0           0            1

name         yearID
role   unused_float
unit               
   0           1979
   1           1975
   2           2000
   3           2000
   4           2001
                ...
4192           2006
4193           2012
4194           2012
4195           2012
4196           1946


4197 rows x 31 columns
memory usage: 0.97 MB
type: getml.DataFrame

In [27]:
salaries["year"] = salaries["yearID"].as_str().as_ts(["%Y"])
salaries["teamIDCat"] = salaries["teamID"]

salaries.set_role(["playerID", "teamID"], getml.data.roles.join_key)
salaries.set_role(["lgID", "teamIDCat"], getml.data.roles.categorical)
salaries.set_role("yearID", getml.data.roles.numerical)
salaries.set_role("salary", getml.data.roles.target)
salaries.set_role("year", getml.data.roles.time_stamp)

salaries

name                          year    playerID     teamID     salary   lgID          teamIDCat        yearID
 role                    time_stamp    join_key   join_key     target   categorical   categorical   numerical
 unit   time stamp, comparison only                                                                          
    0                    1985-01-01   barkele01        ATL     870000   NL            ATL                1985
    1                    1985-01-01   bedrost01        ATL     550000   NL            ATL                1985
    2                    1985-01-01   benedbr01        ATL     545000   NL            ATL                1985
    3                    1985-01-01    campri01        ATL     633333   NL            ATL                1985
    4                    1985-01-01   ceronri01        ATL     625000   NL            ATL                1985
                                ...         ...        ...        ...   ...           ...                 ...
23106                    2012-01-01   tracych01        WAS     750000   NL            WAS                2012
23107                    2012-01-01    wangch01        WAS    4000000   NL            WAS                2012
23108                    2012-01-01   werthja01        WAS   13571428   NL            WAS                2012
23109                    2012-01-01   zimmejo02        WAS    2300000   NL            WAS                2012
23110                    2012-01-01   zimmery01        WAS   12000000   NL            WAS                2012


23111 rows x 7 columns
memory usage: 0.92 MB
type: getml.DataFrame

### 2. Predictive modeling

We loaded the data and defined the roles and units. Next, we create a getML pipeline for relational learning.

In [28]:
split = getml.data.split.random(train=0.8, test=0.2)

#### 2.1 Define relational model

In [29]:
star_schema = getml.data.StarSchema(population=salaries, split=split)

star_schema.join(
    allstarfull,
    on="playerID",
    time_stamps="year",
    horizon=getml.data.time.days(1),
)

star_schema.join(
    awardsplayers,
    on="playerID",
    time_stamps="year",
    horizon=getml.data.time.days(1),
)

star_schema.join(
    awardsshareplayers,
    on="playerID",
    time_stamps="year",
    horizon=getml.data.time.days(1),
)

star_schema.join(
    batting,
    on="playerID",
    time_stamps="year",
    horizon=getml.data.time.days(1),
)

star_schema.join(
    battingpost,
    on="playerID",
    time_stamps="year",
    horizon=getml.data.time.days(1),
)

star_schema.join(
    fielding,
    on="playerID",
    time_stamps="year",
    horizon=getml.data.time.days(1),
)

star_schema.join(
    fieldingpost,
    on="playerID",
    time_stamps="year",
    horizon=getml.data.time.days(1),
)

star_schema.join(
    pitching,
    on="playerID",
    time_stamps="year",
    horizon=getml.data.time.days(1),
)

star_schema.join(
    pitchingpost,
    on="playerID",
    time_stamps="year",
    horizon=getml.data.time.days(1),
)

star_schema

data model

  salaries:
    columns:
    - lgID: categorical
    - teamIDCat: categorical
    - playerID: join_key
    - teamID: join_key
    - yearID: numerical
    - ...

    joins:
    - right: 'allstarfull'
      on: (salaries.playerID, allstarfull.playerID)
      time_stamps: (salaries.year, allstarfull.year)
      relationship: 'many-to-many'
      horizon: 86400.0
      lagged_targets: False
    - right: 'awardsplayers'
      on: (salaries.playerID, awardsplayers.playerID)
      time_stamps: (salaries.year, awardsplayers.year)
      relationship: 'many-to-many'
      horizon: 86400.0
      lagged_targets: False
    - right: 'awardsshareplayers'
      on: (salaries.playerID, awardsshareplayers.playerID)
      time_stamps: (salaries.year, awardsshareplayers.year)
      relationship: 'many-to-many'
      horizon: 86400.0
      lagged_targets: False
    - right: 'batting'
      on: (salaries.playerID, batting.playerID)
      time_stamps: (salaries.year, batting.year)
      relationship: 'many-to-many'
      horizon: 86400.0
      lagged_targets: False
    - right: 'battingpost'
      on: (salaries.playerID, battingpost.playerID)
      time_stamps: (salaries.year, battingpost.year)
      relationship: 'many-to-many'
      horizon: 86400.0
      lagged_targets: False
    - right: 'fielding'
      on: (salaries.playerID, fielding.playerID)
      time_stamps: (salaries.year, fielding.year)
      relationship: 'many-to-many'
      horizon: 86400.0
      lagged_targets: False
    - right: 'fieldingpost'
      on: (salaries.playerID, fieldingpost.playerID)
      time_stamps: (salaries.year, fieldingpost.year)
      relationship: 'many-to-many'
      horizon: 86400.0
      lagged_targets: False
    - right: 'pitching'
      on: (salaries.playerID, pitching.playerID)
      time_stamps: (salaries.year, pitching.year)
      relationship: 'many-to-many'
      horizon: 86400.0
      lagged_targets: False
    - right: 'pitchingpost'
      on: (salaries.playerID, pitchingpost.playerID)
      time_stamps: (salaries.year, pitchingpost.year)
      relationship: 'many-to-many'
      horizon: 86400.0
      lagged_targets: False

  allstarfull:
    columns:
    - gameID: categorical
    - teamID: categorical
    - lgID: categorical
    - playerID: join_key
    - gameNum: numerical
    - ...

  awardsplayers:
    columns:
    - awardID: categorical
    - lgID: categorical
    - notes: categorical
    - playerID: join_key
    - year: time_stamp
    - ...

  awardsshareplayers:
    columns:
    - awardID: categorical
    - lgID: categorical
    - playerID: join_key
    - pointsWon: numerical
    - pointsMax: numerical
    - ...

  batting:
    columns:
    - lgID: categorical
    - playerID: join_key
    - teamID: join_key
    - stint: numerical
    - G: numerical
    - ...

  battingpost:
    columns:
    - round: categorical
    - lgID: categorical
    - playerID: join_key
    - teamID: join_key
    - G: numerical
    - ...

  fielding:
    columns:
    - lgID: categorical
    - POS: categorical
    - playerID: join_key
    - teamID: join_key
    - stint: numerical
    - ...

  fieldingpost:
    columns:
    - lgID: categorical
    - round: categorical
    - POS: categorical
    - playerID: join_key
    - teamID: join_key
    - ...

  pitching:
    columns:
    - lgID: categorical
    - playerID: join_key
    - teamID: join_key
    - stint: numerical
    - W: numerical
    - ...

  pitchingpost:
    columns:
    - round: categorical
    - lgID: categorical
    - playerID: join_key
    - teamID: join_key
    - W: numerical
    - ...


container

  population
      subset   name       rows      type
  0   test     salaries   unknown   View
  1   train    salaries   unknown   View

  peripheral
      name                   rows   type     
  0   allstarfull            4831   DataFrame
  1   awardsplayers          5795   DataFrame
  2   awardsshareplayers     6289   DataFrame
  3   batting               92353   DataFrame
  4   battingpost           

#### 2.2 getML pipeline

<!-- #### 2.1.1  -->
__Set-up the feature learner & predictor__

In [30]:
mapping = getml.preprocessors.Mapping()

fast_prop = getml.feature_learning.FastProp(
    loss_function=getml.feature_learning.loss_functions.SquareLoss,
    num_threads=1,
    num_features=700,
)

relboost = getml.feature_learning.Relboost(
    loss_function=getml.feature_learning.loss_functions.SquareLoss,
    num_threads=1,
    max_depth=8,
)

predictor = getml.predictors.XGBoostRegressor(n_jobs=1)

__Build the pipeline__

In [31]:
pipe1 = getml.pipeline.Pipeline(
    tags=['fast_prop'],
    data_model=star_schema.data_model,
    preprocessors=[mapping],
    feature_learners=[fast_prop],
    predictors=[predictor],
    include_categorical=True,
)

pipe1

Pipeline(data_model='salaries',
         feature_learners=['FastProp'],
         feature_selectors=[],
         include_categorical=True,
         loss_function='SquareLoss',
         peripheral=['allstarfull', 'awardsplayers', 'awardsshareplayers', 'batting',
                     'battingpost', 'fielding', 'fieldingpost', 'pitching', 'pitchingpost'],
         predictors=['XGBoostRegressor'],
         preprocessors=['Mapping'],
         share_selected_features=0.5,
         tags=['fast_prop'])

In [32]:
pipe2 = getml.pipeline.Pipeline(
    tags=['relboost'],
    data_model=star_schema.data_model,
    preprocessors=[mapping],
    feature_learners=[relboost],
    predictors=[predictor],    
    include_categorical=True,
)

pipe2

Pipeline(data_model='salaries',
         feature_learners=['Relboost'],
         feature_selectors=[],
         include_categorical=True,
         loss_function='SquareLoss',
         peripheral=['allstarfull', 'awardsplayers', 'awardsshareplayers', 'batting',
                     'battingpost', 'fielding', 'fieldingpost', 'pitching', 'pitchingpost'],
         predictors=['XGBoostRegressor'],
         preprocessors=['Mapping'],
         share_selected_features=0.5,
         tags=['relboost'])

#### 2.3 Model training

In [33]:
pipe1.check(star_schema.train)

Checking data model...

  Staging... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:00--:--
  Preprocessing... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:01m • 00:0100:01
  Checking... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:005m 94% • 00:01


The pipeline check generated 9 issues labeled INFO and 0 issues labeled WARNING.

type   label                    message                         
0   INFO   FOREIGN KEYS NOT FOUND   When joining SALARIES__STAGING_T...
1   INFO   FOREIGN KEYS NOT FOUND   When joining SALARIES__STAGING_T...
2   INFO   FOREIGN KEYS NOT FOUND   When joining SALARIES__STAGING_T...
3   INFO   FOREIGN KEYS NOT FOUND   When joining SALARIES__STAGING_T...
4   INFO   FOREIGN KEYS NOT FOUND   When joining SALARIES__STAGING_T...
5   INFO   FOREIGN KEYS NOT FOUND   When joining SALARIES__STAGING_T...
6   INFO   FOREIGN KEYS NOT FOUND   When joining SALARIES__STAGING_T...
7   INFO   FOREIGN KEYS NOT FOUND   When joining SALARIES__STAGING_T...
8   INFO   FOREIGN KEYS NOT FOUND   When joining SALARIES__STAGING_T...

In [34]:
pipe1.fit(star_schema.train)

Checking data model...

  Staging... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:0000:00
  Preprocessing... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:00m • 00:0100:01


The pipeline check generated 9 issues labeled INFO and 0 issues labeled WARNING.

To see the issues in full, run .check() on the pipeline.

  Staging... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:0000:00
  Preprocessing... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:00m • 00:0100:01
  FastProp: Trying 3080 features... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:1797% • 00:01
  FastProp: Building features... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:02 • 00:01
  XGBoost: Training as predictor... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:40m • 00:0100:01


Trained pipeline.

Time taken: 0:01:01.081506.



Pipeline(data_model='salaries',
         feature_learners=['FastProp'],
         feature_selectors=[],
         include_categorical=True,
         loss_function='SquareLoss',
         peripheral=['allstarfull', 'awardsplayers', 'awardsshareplayers', 'batting',
                     'battingpost', 'fielding', 'fieldingpost', 'pitching', 'pitchingpost'],
         predictors=['XGBoostRegressor'],
         preprocessors=['Mapping'],
         share_selected_features=0.5,
         tags=['fast_prop', 'container-wPQG4F'])

In [35]:
pipe2.check(star_schema.train)

Checking data model...

  Staging... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:0000:40
  Preprocessing... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:00m • 00:0100:01
  Checking... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:005m 94% • 00:01


The pipeline check generated 9 issues labeled INFO and 0 issues labeled WARNING.

type   label                    message                         
0   INFO   FOREIGN KEYS NOT FOUND   When joining SALARIES__STAGING_T...
1   INFO   FOREIGN KEYS NOT FOUND   When joining SALARIES__STAGING_T...
2   INFO   FOREIGN KEYS NOT FOUND   When joining SALARIES__STAGING_T...
3   INFO   FOREIGN KEYS NOT FOUND   When joining SALARIES__STAGING_T...
4   INFO   FOREIGN KEYS NOT FOUND   When joining SALARIES__STAGING_T...
5   INFO   FOREIGN KEYS NOT FOUND   When joining SALARIES__STAGING_T...
6   INFO   FOREIGN KEYS NOT FOUND   When joining SALARIES__STAGING_T...
7   INFO   FOREIGN KEYS NOT FOUND   When joining SALARIES__STAGING_T...
8   INFO   FOREIGN KEYS NOT FOUND   When joining SALARIES__STAGING_T...

In [36]:
pipe2.fit(star_schema.train)

Checking data model...

  Staging... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:0000:00
  Preprocessing... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:00m • 00:0100:01


The pipeline check generated 9 issues labeled INFO and 0 issues labeled WARNING.

To see the issues in full, run .check() on the pipeline.

  Staging... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:0000:00
  Preprocessing... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:00m • 00:0100:01
  Relboost: Training features... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:55 90% • 00:06
  Relboost: Building features... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:0636m00:0100:01
  XGBoost: Training as predictor... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:03m • 00:0100:01


Trained pipeline.

Time taken: 0:01:06.132155.



Pipeline(data_model='salaries',
         feature_learners=['Relboost'],
         feature_selectors=[],
         include_categorical=True,
         loss_function='SquareLoss',
         peripheral=['allstarfull', 'awardsplayers', 'awardsshareplayers', 'batting',
                     'battingpost', 'fielding', 'fieldingpost', 'pitching', 'pitchingpost'],
         predictors=['XGBoostRegressor'],
         preprocessors=['Mapping'],
         share_selected_features=0.5,
         tags=['relboost', 'container-wPQG4F'])

#### 2.4 Model evaluation

In [37]:
fastprop_score = pipe1.score(star_schema.test)
fastprop_score

  Staging... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:00--:--
  Preprocessing... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:00m • 00:0100:01
  FastProp: Building features... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:0200:00


date time             set used   target            mae            rmse   rsquared
0   2024-09-03 15:14:33   train      salary    693195.922     1251354.7312     0.8222
1   2024-09-03 15:15:44   test       salary    764427.8758    1400878.9269     0.7886

In [38]:
relboost_score = pipe2.score(star_schema.test)
relboost_score

  Staging... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:0000:02
  Preprocessing... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:00m • 00:0100:01
  Relboost: Building features... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:0136m00:0100:01


date time             set used   target            mae            rmse   rsquared
0   2024-09-03 15:15:40   train      salary    457056.2274     797759.2501     0.9276
1   2024-09-03 15:15:47   test       salary    664777.8524    1214580.8821     0.8411

#### 2.5 featuretools

In [39]:
population_train_pd = star_schema.train.population.to_pandas()
population_test_pd = star_schema.test.population.to_pandas()

In [40]:
allstarfull_pd = allstarfull.drop(allstarfull.roles.unused).to_pandas()
awardsplayers_pd = awardsplayers.drop(awardsplayers.roles.unused).to_pandas()
awardsshareplayers_pd = awardsshareplayers.drop(awardsshareplayers.roles.unused).to_pandas()
batting_pd = batting.drop(batting.roles.unused).to_pandas()
battingpost_pd = battingpost.drop(battingpost.roles.unused).to_pandas()
fielding_pd = fielding.drop(fielding.roles.unused).to_pandas()
fieldingpost_pd = fieldingpost.drop(fieldingpost.roles.unused).to_pandas()
pitching_pd = pitching.drop(pitching.roles.unused).to_pandas()
pitchingpost_pd = pitchingpost.drop(pitchingpost.roles.unused).to_pandas()

featuretools requires that we manually define a primary key and then join on that primary key. Therefore, we need some manual data preparation.

In [41]:
population_train_pd["id"] = population_train_pd.index
population_train_pd

lgID teamIDCat   playerID teamID  yearID      salary       year     id
0       NL       ATL  barkele01    ATL  1985.0    870000.0 1985-01-01      0
1       NL       ATL  bedrost01    ATL  1985.0    550000.0 1985-01-01      1
2       NL       ATL  benedbr01    ATL  1985.0    545000.0 1985-01-01      2
3       NL       ATL  ceronri01    ATL  1985.0    625000.0 1985-01-01      3
4       NL       ATL  chambch01    ATL  1985.0    800000.0 1985-01-01      4
...    ...       ...        ...    ...     ...         ...        ...    ...
18567   NL       WAS  strasst01    WAS  2012.0   4875000.0 2012-01-01  18567
18568   NL       WAS  tracych01    WAS  2012.0    750000.0 2012-01-01  18568
18569   NL       WAS   wangch01    WAS  2012.0   4000000.0 2012-01-01  18569
18570   NL       WAS  werthja01    WAS  2012.0  13571428.0 2012-01-01  18570
18571   NL       WAS  zimmery01    WAS  2012.0  12000000.0 2012-01-01  18571

[18572 rows x 8 columns]

In [42]:
population_test_pd["id"] = population_test_pd.index
population_test_pd

lgID teamIDCat   playerID teamID  yearID     salary       year    id
0      NL       ATL   campri01    ATL  1985.0   633333.0 1985-01-01     0
1      NL       ATL  dedmoje01    ATL  1985.0   150000.0 1985-01-01     1
2      NL       ATL  hornebo01    ATL  1985.0  1500000.0 1985-01-01     2
3      AL       BAL  dempsri01    BAL  1985.0   512500.0 1985-01-01     3
4      AL       BAL  martide01    BAL  1985.0   560000.0 1985-01-01     4
...   ...       ...        ...    ...     ...        ...        ...   ...
4534   NL       WAS  desmoia01    WAS  2012.0   512500.0 2012-01-01  4534
4535   NL       WAS  espinda01    WAS  2012.0   506000.0 2012-01-01  4535
4536   NL       WAS  gorzeto01    WAS  2012.0  3000000.0 2012-01-01  4536
4537   NL       WAS  matthry01    WAS  2012.0   481000.0 2012-01-01  4537
4538   NL       WAS  zimmejo02    WAS  2012.0  2300000.0 2012-01-01  4538

[4539 rows x 8 columns]

In [43]:
def prepare_peripheral(peripheral_pd, train_or_test):
    """
    Helper function that imitates the behavior of 
    the data model defined above.
    """
    peripheral_new = peripheral_pd.merge(
        train_or_test[["id", "playerID", "year"]],
        on="playerID"
    )

    peripheral_new = peripheral_new[
        peripheral_new["year_x"] < peripheral_new["year_y"]
    ]

    del peripheral_new["year_x"]
    del peripheral_new["year_y"]
    del peripheral_new["playerID"]

    return peripheral_new

In [44]:
allstarfull_train_pd = prepare_peripheral(allstarfull_pd, population_train_pd)
allstarfull_test_pd = prepare_peripheral(allstarfull_pd, population_test_pd)
allstarfull_train_pd

gameID teamID lgID  gameNum   GP  startingPos     id
1      NLS198607150    BAL   AL      0.0  1.0          NaN   1051
2      NLS198607150    BAL   AL      0.0  1.0          NaN   1569
3      NLS198607150    BAL   AL      0.0  1.0          NaN   2426
11     NLS200407130    PHI   NL      0.0  1.0          NaN  13684
12     NLS200407130    PHI   NL      0.0  1.0          NaN  14357
...             ...    ...  ...      ...  ...          ...    ...
20490  NLS200607110    OAK   AL      0.0  1.0          NaN  17789
20491  NLS200607110    OAK   AL      0.0  1.0          NaN  18456
20494  NLS200907140    TBA   AL      0.0  1.0          NaN  17158
20495  NLS200907140    TBA   AL      0.0  1.0          NaN  17836
20496  NLS200907140    TBA   AL      0.0  1.0          NaN  18502

[11557 rows x 7 columns]

In [45]:
awardsplayers_train_pd = prepare_peripheral(awardsplayers_pd, population_train_pd)
awardsplayers_test_pd = prepare_peripheral(awardsplayers_pd, population_test_pd)
awardsplayers_train_pd

awardID lgID notes     id
0                   TSN Player of the Year   AL  None   4683
1                   TSN Player of the Year   AL  None   5856
2                   TSN Player of the Year   AL  None   8922
3                   TSN Player of the Year   AL  None   9727
4                       Rookie of the Year   NL  None    120
...                                    ...  ...   ...    ...
26073                       Silver Slugger   NL    1B  18120
26080                       Silver Slugger   NL     C  17943
26086                       Silver Slugger   NL    2B  18064
26104  TSN Major League Player of the Year   ML  None  18134
26110              TSN Pitcher of the Year   AL  None  18134

[15639 rows x 4 columns]

In [46]:
awardsshareplayers_train_pd = prepare_peripheral(awardsshareplayers_pd, population_train_pd)
awardsshareplayers_test_pd = prepare_peripheral(awardsshareplayers_pd, population_test_pd)
awardsshareplayers_train_pd

awardID lgID  pointsWon  pointsMax  votesFirst     id
0                Cy Young   NL        1.0       24.0         1.0    254
1                Cy Young   NL        1.0       24.0         1.0    614
2                Cy Young   NL       23.0       24.0        23.0    548
3                Cy Young   NL        4.0      120.0         0.0    548
4                Cy Young   AL       98.0      120.0        14.0    361
...                   ...  ...        ...        ...         ...    ...
24216  Rookie of the Year   NL      158.0      160.0        31.0  16676
24217  Rookie of the Year   NL      158.0      160.0        31.0  17347
24218  Rookie of the Year   NL        9.0      160.0         0.0  16703
24219  Rookie of the Year   NL        9.0      160.0         0.0  17370
24220  Rookie of the Year   NL        9.0      160.0         0.0  18404

[15527 rows x 6 columns]

In [47]:
batting_train_pd = prepare_peripheral(batting_pd, population_train_pd)
batting_test_pd = prepare_peripheral(batting_pd, population_test_pd)
batting_train_pd

lgID teamID  stint     G  G_batting     AB     R     H   2B   3B  ...  \
1        NL    SFN    1.0  11.0       11.0    0.0   0.0   0.0  0.0  0.0  ...   
2        NL    SFN    1.0  11.0       11.0    0.0   0.0   0.0  0.0  0.0  ...   
3        NL    SFN    1.0  11.0       11.0    0.0   0.0   0.0  0.0  0.0  ...   
4        NL    SFN    1.0  11.0       11.0    0.0   0.0   0.0  0.0  0.0  ...   
5        NL    SFN    1.0  11.0       11.0    0.0   0.0   0.0  0.0  0.0  ...   
...     ...    ...    ...   ...        ...    ...   ...   ...  ...  ...  ...   
208118   NL    ATL    1.0  11.0       11.0   25.0   2.0   5.0  1.0  0.0  ...   
208119   NL    ATL    1.0  81.0       81.0  190.0  16.0  48.0  8.0  1.0  ...   
208120   AL    NYA    1.0  21.0       21.0   48.0   2.0   4.0  1.0  0.0  ...   
208121   AL    NYA    1.0  14.0       14.0   34.0   2.0   6.0  0.0  0.0  ...   
208122   AL    CLE    1.0  51.0       51.0  130.0   9.0  30.0  5.0  1.0  ...   

         CS    BB    SO  IBB  HBP   SH   SF  GIDP  G_old     id  
1       0.0   0.0   0.0  0.0  0.0  0.0  0.0   0.0   11.0  14656  
2       0.0   0.0   0.0  0.0  0.0  0.0  0.0   0.0   11.0  16389  
3       0.0   0.0   0.0  0.0  0.0  0.0  0.0   0.0   11.0  17069  
4       0.0   0.0   0.0  0.0  0.0  0.0  0.0   0.0   11.0  17743  
5       0.0   0.0   0.0  0.0  0.0  0.0  0.0   0.0   11.0  18263  
...     ...   ...   ...  ...  ...  ...  ...   ...    ...    ...  
208118  0.0   2.0   3.0  0.0  0.0  0.0  0.0   0.0   11.0   2109  
208119  0.0  16.0  14.0  1.0  0.0  4.0  0.0   3.0   81.0   2109  
208120  0.0   5.0   4.0  0.0  0.0  4.0  0.0   1.0   21.0   2109  
208121  0.0   0.0   4.0  0.0  0.0  2.0  0.0   1.0   14.0   2109  
208122  0.0   8.0  13.0  0.0  0.0  8.0  0.0   3.0   51.0   2109  

[105808 rows x 23 columns]

In [48]:
battingpost_train_pd = prepare_peripheral(battingpost_pd, population_train_pd)
battingpost_test_pd = prepare_peripheral(battingpost_pd, population_test_pd)
battingpost_train_pd

round lgID teamID    G    AB    R    H   2B   3B   HR  ...   SB   CS  \
0        WS   NL    SLN  1.0   1.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
1        WS   NL    SLN  1.0   1.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
2        WS   NL    SLN  2.0   0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
3        WS   NL    SLN  2.0   0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
4      ALCS   AL    MIN  3.0  14.0  0.0  1.0  0.0  0.0  0.0  ...  0.0  0.0   
...     ...  ...    ...  ...   ...  ...  ...  ...  ...  ...  ...  ...  ...   
48498    WS   AL    TEX  1.0   0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
48517    WS   NL    SLN  6.0  14.0  0.0  3.0  0.0  0.0  0.0  ...  0.0  0.0   
48546    WS   NL    SLN  5.0  13.0  1.0  1.0  0.0  0.0  0.0  ...  0.0  0.0   
48554    WS   AL    TEX  3.0   5.0  0.0  2.0  0.0  0.0  0.0  ...  0.0  0.0   
48575    WS   AL    TEX  7.0  27.0  3.0  7.0  4.0  0.0  1.0  ...  0.0  0.0   

        BB   SO  IBB  HBP   SH   SF  GIDP     id  
0      0.0  0.0  0.0  0.0  0.0  0.0   0.0    301  
1      0.0  0.0  0.0  0.0  0.0  0.0   0.0    533  
2      0.0  0.0  0.0  0.0  0.0  0.0   0.0    301  
3      0.0  0.0  0.0  0.0  0.0  0.0   0.0    533  
4      1.0  4.0  0.0  0.0  0.0  0.0   0.0     59  
...    ...  ...  ...  ...  ...  ...   ...    ...  
48498  0.0  0.0  NaN  NaN  NaN  NaN   NaN  18542  
48517  5.0  6.0  NaN  NaN  NaN  NaN   NaN  18001  
48546  1.0  3.0  NaN  NaN  NaN  NaN   NaN  18453  
48554  1.0  2.0  NaN  NaN  NaN  NaN   NaN  18525  
48575  1.0  7.0  NaN  NaN  NaN  NaN   NaN  18527  

[22893 rows x 21 columns]

In [49]:
fielding_train_pd = prepare_peripheral(fielding_pd, population_train_pd)
fielding_test_pd = prepare_peripheral(fielding_pd, population_test_pd)
fielding_train_pd

lgID POS teamID  stint     G    GS  InnOuts    PO      A    E    DP  \
1        NL   P    SFN    1.0  11.0   0.0     32.0   0.0    0.0  0.0   0.0   
2        NL   P    SFN    1.0  11.0   0.0     32.0   0.0    0.0  0.0   0.0   
3        NL   P    SFN    1.0  11.0   0.0     32.0   0.0    0.0  0.0   0.0   
4        NL   P    SFN    1.0  11.0   0.0     32.0   0.0    0.0  0.0   0.0   
5        NL   P    SFN    1.0  11.0   0.0     32.0   0.0    0.0  0.0   0.0   
...     ...  ..    ...    ...   ...   ...      ...   ...    ...  ...   ...   
361010   AL  SS    NYA    1.0  21.0  18.0    453.0  30.0   54.0  3.0  12.0   
361011   AL  2B    NYA    1.0   7.0   6.0    168.0  17.0   18.0  0.0   5.0   
361012   AL  3B    NYA    1.0   1.0   0.0      3.0   0.0    0.0  0.0   0.0   
361013   AL  SS    NYA    1.0   6.0   1.0     70.0   3.0    7.0  0.0   0.0   
361014   AL  SS    CLE    1.0  49.0  44.0   1139.0  77.0  112.0  8.0  21.0   

           id  
1       14656  
2       16389  
3       17069  
4       17743  
5       18263  
...       ...  
361010   2109  
361011   2109  
361012   2109  
361013   2109  
361014   2109  

[182144 rows x 12 columns]

In [50]:
fieldingpost_train_pd = prepare_peripheral(fieldingpost_pd, population_train_pd)
fieldingpost_test_pd = prepare_peripheral(fieldingpost_pd, population_test_pd)
fieldingpost_train_pd

lgID  round POS teamID    G   GS  InnOuts   PO    A    E   DP   TP   SB  \
0       AL   ALCS   P    CAL  2.0  0.0     15.0  0.0  1.0  0.0  0.0  0.0  0.0   
1       AL   ALCS   P    CAL  2.0  0.0     15.0  0.0  1.0  0.0  0.0  0.0  0.0   
2       AL   ALCS   P    CAL  2.0  0.0     15.0  0.0  1.0  0.0  0.0  0.0  0.0   
3       AL   ALCS   P    CAL  2.0  0.0     15.0  0.0  1.0  0.0  0.0  0.0  0.0   
11      NL   NLCS  2B    FLO  2.0  2.0     51.0  4.0  1.0  0.0  0.0  0.0  NaN   
...    ...    ...  ..    ...  ...  ...      ...  ...  ...  ...  ...  ...  ...   
58087   AL   ALCS   P    OAK  1.0  1.0     11.0  0.0  2.0  0.0  0.0  0.0  0.0   
58088   AL   ALCS   P    OAK  1.0  1.0     11.0  0.0  2.0  0.0  0.0  0.0  0.0   
58095   AL  ALDS2   P    OAK  1.0  1.0     24.0  0.0  1.0  0.0  0.0  0.0  0.0   
58096   AL  ALDS2   P    OAK  1.0  1.0     24.0  0.0  1.0  0.0  0.0  0.0  0.0   
58097   AL  ALDS2   P    OAK  1.0  1.0     24.0  0.0  1.0  0.0  0.0  0.0  0.0   

        CS     id  
0      0.0    454  
1      0.0   1051  
2      0.0   1569  
3      0.0   2426  
11     NaN   8818  
...    ...    ...  
58087  0.0  17789  
58088  0.0  18456  
58095  1.0  17114  
58096  1.0  17789  
58097  1.0  18456  

[27491 rows x 15 columns]

In [51]:
pitching_train_pd = prepare_peripheral(pitching_pd, population_train_pd)
pitching_test_pd = prepare_peripheral(pitching_pd, population_test_pd)
pitching_train_pd

lgID teamID  stint     W     L     G    GS   CG  SHO   SV  ...  BAOpp  \
1       NL    SFN    1.0   1.0   0.0  11.0   0.0  0.0  0.0  0.0  ...    0.0   
2       NL    SFN    1.0   1.0   0.0  11.0   0.0  0.0  0.0  0.0  ...    0.0   
3       NL    SFN    1.0   1.0   0.0  11.0   0.0  0.0  0.0  0.0  ...    0.0   
4       NL    SFN    1.0   1.0   0.0  11.0   0.0  0.0  0.0  0.0  ...    0.0   
5       NL    SFN    1.0   1.0   0.0  11.0   0.0  0.0  0.0  0.0  ...    0.0   
...    ...    ...    ...   ...   ...   ...   ...  ...  ...  ...  ...    ...   
91802   NL    SFN    1.0  10.0  13.0  33.0  33.0  1.0  0.0  0.0  ...    NaN   
91803   NL    SFN    1.0  10.0  13.0  33.0  33.0  1.0  0.0  0.0  ...    NaN   
91811   NL    SFN    1.0   9.0  14.0  34.0  33.0  1.0  0.0  0.0  ...    NaN   
91812   NL    SFN    1.0   9.0  14.0  34.0  33.0  1.0  0.0  0.0  ...    NaN   
91821   NL    SFN    1.0   3.0   4.0  13.0   9.0  0.0  0.0  0.0  ...    NaN   

       ERA  IBB   WP  HBP   BK    BFP   GF     R     id  
1      6.0  0.0  0.0  2.0  0.0   61.0  5.0   8.0  14656  
2      6.0  0.0  0.0  2.0  0.0   61.0  5.0   8.0  16389  
3      6.0  0.0  0.0  2.0  0.0   61.0  5.0   8.0  17069  
4      6.0  0.0  0.0  2.0  0.0   61.0  5.0   8.0  17743  
5      6.0  0.0  0.0  2.0  0.0   61.0  5.0   8.0  18263  
...    ...  ...  ...  ...  ...    ...  ...   ...    ...  
91802  4.0  8.0  2.0  8.0  2.0  818.0  0.0  89.0  17789  
91803  4.0  8.0  2.0  8.0  2.0  818.0  0.0  89.0  18456  
91811  4.0  7.0  7.0  7.0  0.0  848.0  1.0  97.0  17789  
91812  4.0  7.0  7.0  7.0  0.0  848.0  1.0  97.0  18456  
91821  5.0  1.0  1.0  0.0  0.0  225.0  3.0  35.0  18456  

[45669 rows x 26 columns]

In [52]:
pitchingpost_train_pd = prepare_peripheral(pitchingpost_pd, population_train_pd)
pitchingpost_test_pd = prepare_peripheral(pitchingpost_pd, population_test_pd)
pitchingpost_train_pd

round lgID teamID    W    L    G   GS   CG  SHO   SV  ...   WP  HBP  \
0       ALCS   AL    CAL  1.0  0.0  2.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
1       ALCS   AL    CAL  1.0  0.0  2.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
2       ALCS   AL    CAL  1.0  0.0  2.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
3       ALCS   AL    CAL  1.0  0.0  2.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
7       ALCS   AL    SEA  0.0  1.0  1.0  1.0  0.0  0.0  0.0  ...  0.0  0.0   
...      ...  ...    ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
24239   ALCS   AL    OAK  0.0  1.0  1.0  1.0  0.0  0.0  0.0  ...  0.0  0.0   
24240   ALCS   AL    OAK  0.0  1.0  1.0  1.0  0.0  0.0  0.0  ...  0.0  0.0   
24247  ALDS2   AL    OAK  1.0  0.0  1.0  1.0  0.0  0.0  0.0  ...  0.0  0.0   
24248  ALDS2   AL    OAK  1.0  0.0  1.0  1.0  0.0  0.0  0.0  ...  0.0  0.0   
24249  ALDS2   AL    OAK  1.0  0.0  1.0  1.0  0.0  0.0  0.0  ...  0.0  0.0   

        BK   BFP   GF    R   SH   SF  GIDP     id  
0      0.0  20.0  2.0  1.0  0.0  1.0   0.0    454  
1      0.0  20.0  2.0  1.0  0.0  1.0   0.0   1051  
2      0.0  20.0  2.0  1.0  0.0  1.0   0.0   1569  
3      0.0  20.0  2.0  1.0  0.0  1.0   0.0   2426  
7      0.0  21.0  0.0  3.0  0.0  0.0   0.0  11801  
...    ...   ...  ...  ...  ...  ...   ...    ...  
24239  0.0  21.0  0.0  5.0  0.0  0.0   0.0  17789  
24240  0.0  21.0  0.0  5.0  0.0  0.0   0.0  18456  
24247  0.0  30.0  0.0  1.0  1.0  0.0   0.0  17114  
24248  0.0  30.0  0.0  1.0  1.0  0.0   0.0  17789  
24249  0.0  30.0  0.0  1.0  1.0  0.0   0.0  18456  

[11364 rows x 29 columns]

In [53]:
population_train_pd

lgID teamIDCat   playerID teamID  yearID      salary       year     id
0       NL       ATL  barkele01    ATL  1985.0    870000.0 1985-01-01      0
1       NL       ATL  bedrost01    ATL  1985.0    550000.0 1985-01-01      1
2       NL       ATL  benedbr01    ATL  1985.0    545000.0 1985-01-01      2
3       NL       ATL  ceronri01    ATL  1985.0    625000.0 1985-01-01      3
4       NL       ATL  chambch01    ATL  1985.0    800000.0 1985-01-01      4
...    ...       ...        ...    ...     ...         ...        ...    ...
18567   NL       WAS  strasst01    WAS  2012.0   4875000.0 2012-01-01  18567
18568   NL       WAS  tracych01    WAS  2012.0    750000.0 2012-01-01  18568
18569   NL       WAS   wangch01    WAS  2012.0   4000000.0 2012-01-01  18569
18570   NL       WAS  werthja01    WAS  2012.0  13571428.0 2012-01-01  18570
18571   NL       WAS  zimmery01    WAS  2012.0  12000000.0 2012-01-01  18571

[18572 rows x 8 columns]

In [54]:
def add_index(df):
    df.insert(0, "index", range(len(df)))

population_pd_logical_types = {
    'lgID': ww.logical_types.Categorical,
    'teamIDCat': ww.logical_types.Categorical,
    'playerID': ww.logical_types.Categorical,
    'teamID': ww.logical_types.Categorical,
    'yearID': ww.logical_types.Integer,
    'salary': ww.logical_types.IntegerNullable,
    'year': ww.logical_types.Datetime,
    'id': ww.logical_types.Integer
}
population_test_pd.ww.init(logical_types=population_pd_logical_types, index='id', name='population')
population_train_pd.ww.init(logical_types=population_pd_logical_types, index='id', name='population')

add_index(allstarfull_test_pd)
add_index(allstarfull_train_pd)
allstarfull_pd_logical_types = {
    'index': ww.logical_types.Integer,
    'gameID': ww.logical_types.Categorical,
    'teamID': ww.logical_types.Categorical,
    'lgID': ww.logical_types.Categorical,
    'gameNum': ww.logical_types.Categorical,
    'GP': ww.logical_types.Categorical,
    'startingPos': ww.logical_types.Categorical,
    'id': ww.logical_types.Integer
}
allstarfull_test_pd.ww.init(logical_types=allstarfull_pd_logical_types, index='index', name='allstarfull')
allstarfull_train_pd.ww.init(logical_types=allstarfull_pd_logical_types, index='index', name='allstarfull')

add_index(awardsplayers_test_pd)
add_index(awardsplayers_train_pd)
awardsplayers_pd_logical_types = {
    'index': ww.logical_types.Integer,
    'awardID': ww.logical_types.Categorical,
    'lgID': ww.logical_types.Categorical,
    'notes': ww.logical_types.Categorical,
    'id': ww.logical_types.Integer
}
awardsplayers_test_pd.ww.init(logical_types=awardsplayers_pd_logical_types, index='index', name='awardsplayers')
awardsplayers_train_pd.ww.init(logical_types=awardsplayers_pd_logical_types, index='index', name='awardsplayers')

add_index(awardsshareplayers_test_pd)
add_index(awardsshareplayers_train_pd)
awardsshareplayers_pd_logical_types = {
    'index': ww.logical_types.Integer,
    'awardID': ww.logical_types.Categorical,
    'lgID': ww.logical_types.Categorical,
    'pointsWon': ww.logical_types.IntegerNullable,
    'pointsMax': ww.logical_types.Categorical,
    'votesFirst': ww.logical_types.IntegerNullable,
    'id': ww.logical_types.Integer
}
awardsshareplayers_test_pd.ww.init(logical_types=awardsshareplayers_pd_logical_types, index='index', name='awardsshareplayers')
awardsshareplayers_train_pd.ww.init(logical_types=awardsshareplayers_pd_logical_types, index='index', name='awardsshareplayers')

add_index(batting_test_pd)
add_index(batting_train_pd)
batting_pd_logical_types = {
    'index': ww.logical_types.Integer,
    'lgID': ww.logical_types.Categorical,
    'teamID': ww.logical_types.Categorical,
    'stint': ww.logical_types.Categorical,
    'G': ww.logical_types.IntegerNullable,
    'G_batting': ww.logical_types.IntegerNullable,
    'AB': ww.logical_types.IntegerNullable,
    'R': ww.logical_types.IntegerNullable,
    'H': ww.logical_types.IntegerNullable,
    '2B': ww.logical_types.IntegerNullable,
    '3B': ww.logical_types.IntegerNullable,
    'HR': ww.logical_types.IntegerNullable,
    'RBI': ww.logical_types.IntegerNullable,
    'SB': ww.logical_types.IntegerNullable,
    'CS': ww.logical_types.IntegerNullable,
    'BB': ww.logical_types.IntegerNullable,
    'SO': ww.logical_types.IntegerNullable,
    'IBB': ww.logical_types.IntegerNullable,
    'HBP': ww.logical_types.IntegerNullable,
    'SH': ww.logical_types.IntegerNullable,
    'SF': ww.logical_types.IntegerNullable,
    'GIDP': ww.logical_types.IntegerNullable,
    'G_old': ww.logical_types.IntegerNullable,
    'id': ww.logical_types.Integer
}
batting_test_pd.ww.init(logical_types=batting_pd_logical_types, index='index', name='batting')
batting_train_pd.ww.init(logical_types=batting_pd_logical_types, index='index', name='batting')

add_index(battingpost_test_pd)
add_index(battingpost_train_pd)
battingpost_pd_logical_types = {
    'index': ww.logical_types.Integer,
    'round': ww.logical_types.Categorical,
    'lgID': ww.logical_types.Categorical,
    'teamID': ww.logical_types.Categorical,
    'G': ww.logical_types.IntegerNullable,
    'AB': ww.logical_types.IntegerNullable,
    'R': ww.logical_types.IntegerNullable,
    'H': ww.logical_types.IntegerNullable,
    '2B': ww.logical_types.IntegerNullable,
    '3B': ww.logical_types.IntegerNullable,
    'HR': ww.logical_types.IntegerNullable,
    'RBI': ww.logical_types.IntegerNullable,
    'SB': ww.logical_types.IntegerNullable,
    'CS': ww.logical_types.IntegerNullable,
    'BB': ww.logical_types.IntegerNullable,
    'SO': ww.logical_types.IntegerNullable,
    'IBB': ww.logical_types.IntegerNullable,
    'HBP': ww.logical_types.IntegerNullable,
    'SH': ww.logical_types.IntegerNullable,
    'SF': ww.logical_types.IntegerNullable,
    'GIDP': ww.logical_types.IntegerNullable,
    'id': ww.logical_types.Integer
}
battingpost_test_pd.ww.init(logical_types=battingpost_pd_logical_types, index='index', name='battingpost')
battingpost_train_pd.ww.init(logical_types=battingpost_pd_logical_types, index='index', name='battingpost')

add_index(fielding_test_pd)
add_index(fielding_train_pd)
fielding_pd_logical_types = {
    'index': ww.logical_types.Integer,
    'lgID': ww.logical_types.Categorical,
    'POS': ww.logical_types.Categorical,
    'teamID': ww.logical_types.Categorical,
    'stint': ww.logical_types.Categorical,
    'G': ww.logical_types.IntegerNullable,
    'GS': ww.logical_types.IntegerNullable,
    'InnOuts': ww.logical_types.IntegerNullable,
    'PO': ww.logical_types.IntegerNullable,
    'A': ww.logical_types.IntegerNullable,
    'E': ww.logical_types.IntegerNullable,
    'DP': ww.logical_types.IntegerNullable,
    'id': ww.logical_types.Integer
}
fielding_test_pd.ww.init(logical_types=fielding_pd_logical_types, index='index', name='fielding')
fielding_train_pd.ww.init(logical_types=fielding_pd_logical_types, index='index', name='fielding')

add_index(fieldingpost_test_pd)
add_index(fieldingpost_train_pd)
fieldingpost_pd_logical_types = {
    'index': ww.logical_types.Integer,
    'lgID': ww.logical_types.Categorical,
    'round': ww.logical_types.Categorical,
    'POS': ww.logical_types.Categorical,
    'teamID': ww.logical_types.Categorical,
    'G': ww.logical_types.IntegerNullable,
    'GS': ww.logical_types.IntegerNullable,
    'InnOuts': ww.logical_types.IntegerNullable,
    'PO': ww.logical_types.IntegerNullable,
    'A': ww.logical_types.IntegerNullable,
    'E': ww.logical_types.IntegerNullable,
    'DP': ww.logical_types.IntegerNullable,
    'TP': ww.logical_types.IntegerNullable,
    'SB': ww.logical_types.IntegerNullable,
    'CS': ww.logical_types.IntegerNullable,
    'id': ww.logical_types.Integer
}
fieldingpost_test_pd.ww.init(logical_types=fieldingpost_pd_logical_types, index='index', name='fieldingpost')
fieldingpost_train_pd.ww.init(logical_types=fieldingpost_pd_logical_types, index='index', name='fieldingpost')

add_index(pitching_test_pd)
add_index(pitching_train_pd)
pitching_pd_logical_types = {
    'index': ww.logical_types.Integer,
    'lgID': ww.logical_types.Categorical,
    'teamID': ww.logical_types.Categorical,
    'stint': ww.logical_types.Categorical,
    'W': ww.logical_types.IntegerNullable,
    'L': ww.logical_types.IntegerNullable,
    'G': ww.logical_types.IntegerNullable,
    'GS': ww.logical_types.IntegerNullable,
    'CG': ww.logical_types.IntegerNullable,
    'SHO': ww.logical_types.IntegerNullable,
    'SV': ww.logical_types.IntegerNullable,
    'IPouts': ww.logical_types.IntegerNullable,
    'H': ww.logical_types.IntegerNullable,
    'ER': ww.logical_types.IntegerNullable,
    'HR': ww.logical_types.IntegerNullable,
    'BB': ww.logical_types.IntegerNullable,
    'SO': ww.logical_types.IntegerNullable,
    'BAOpp': ww.logical_types.IntegerNullable,
    'ERA': ww.logical_types.IntegerNullable,
    'IBB': ww.logical_types.IntegerNullable,
    'WP': ww.logical_types.IntegerNullable,
    'HBP': ww.logical_types.IntegerNullable,
    'BK': ww.logical_types.IntegerNullable,
    'BFP': ww.logical_types.IntegerNullable,
    'GF': ww.logical_types.IntegerNullable,
    'R': ww.logical_types.IntegerNullable,
    'id': ww.logical_types.Integer
}
pitching_test_pd.ww.init(logical_types=pitching_pd_logical_types, index='index', name='pitching')
pitching_train_pd.ww.init(logical_types=pitching_pd_logical_types, index='index', name='pitching')

add_index(pitchingpost_test_pd)
add_index(pitchingpost_train_pd)
pitchingpost_pd_logical_types = {
    'index': ww.logical_types.Integer,
    'round': ww.logical_types.Categorical,
    'lgID': ww.logical_types.Categorical,
    'teamID': ww.logical_types.Categorical,
    'W': ww.logical_types.IntegerNullable,
    'L': ww.logical_types.IntegerNullable,
    'G': ww.logical_types.IntegerNullable,
    'GS': ww.logical_types.IntegerNullable,
    'CG': ww.logical_types.IntegerNullable,
    'SHO': ww.logical_types.IntegerNullable,
    'SV': ww.logical_types.IntegerNullable,
    'IPouts': ww.logical_types.IntegerNullable,
    'H': ww.logical_types.IntegerNullable,
    'ER': ww.logical_types.IntegerNullable,
    'HR': ww.logical_types.IntegerNullable,
    'BB': ww.logical_types.IntegerNullable,
    'SO': ww.logical_types.IntegerNullable,
    'BAOpp': ww.logical_types.IntegerNullable,
    'ERA': ww.logical_types.IntegerNullable,
    'IBB': ww.logical_types.IntegerNullable,
    'WP': ww.logical_types.IntegerNullable,
    'HBP': ww.logical_types.IntegerNullable,
    'BK': ww.logical_types.IntegerNullable,
    'BFP': ww.logical_types.IntegerNullable,
    'GF': ww.logical_types.IntegerNullable,
    'R': ww.logical_types.Double,
    'SH': ww.logical_types.IntegerNullable,
    'SF': ww.logical_types.IntegerNullable,
    'GIDP': ww.logical_types.IntegerNullable,
    'id': ww.logical_types.Integer
}
pitchingpost_test_pd.ww.init(logical_types=pitchingpost_pd_logical_types, index='index', name='pitchingpost')
pitchingpost_train_pd.ww.init(logical_types=pitchingpost_pd_logical_types, index='index', name='pitchingpost')

In [55]:
dataframes_train = {
    "population" : (population_train_pd, ),
    "allstarfull": (allstarfull_train_pd, ),
    "awardsplayers": (awardsplayers_train_pd, ),
    "awardsshareplayers": (awardsshareplayers_train_pd, ),
    "batting": (batting_train_pd, ),
    "battingpost": (battingpost_train_pd, ),
    "fielding": (fielding_train_pd, ),
    "fieldingpost": (fieldingpost_train_pd, ),
    "pitching": (pitching_train_pd, ),
    "pitchingpost": (pitchingpost_train_pd, ),
}

In [56]:
dataframes_test = {
    "population" : (population_test_pd, ),
    "allstarfull": (allstarfull_test_pd, ),
    "awardsplayers": (awardsplayers_test_pd, ),
    "awardsshareplayers": (awardsshareplayers_test_pd, ),
    "batting": (batting_test_pd, ),
    "battingpost": (battingpost_test_pd, ),
    "fielding": (fielding_test_pd, ),
    "fieldingpost": (fieldingpost_test_pd, ),
    "pitching": (pitching_test_pd, ),
    "pitchingpost": (pitchingpost_test_pd, ),
}

In [57]:
relationships = [
    ("population", "id", "allstarfull", "id"),
    ("population", "id", "awardsplayers", "id"),
    ("population", "id", "awardsshareplayers", "id"),
    ("population", "id", "batting", "id"),
    ("population", "id", "battingpost", "id"),
    ("population", "id", "fielding", "id"),
    ("population", "id", "fieldingpost", "id"),
    ("population", "id", "pitching", "id"),
    ("population", "id", "pitchingpost", "id"),
]

In [58]:
featuretools_train_pd = featuretools.dfs(
    dataframes=dataframes_train,
    relationships=relationships,
    target_dataframe_name="population")[0]

In [59]:
featuretools_test_pd = featuretools.dfs(
    dataframes=dataframes_test,
    relationships=relationships,
    target_dataframe_name="population")[0]

In [60]:
featuretools_train_pd.replace([np.inf, -np.inf], np.nan, inplace=True)
featuretools_test_pd.replace([np.inf, -np.inf], np.nan, inplace=True)

In [61]:
featuretools_train = getml.data.DataFrame.from_pandas(featuretools_train_pd, "featuretools_train")
featuretools_test = getml.data.DataFrame.from_pandas(featuretools_test_pd, "featuretools_test")

In [62]:
featuretools_train.set_role("salary", getml.data.roles.target)
featuretools_train.set_role(featuretools_train.roles.unused_float, getml.data.roles.numerical)
featuretools_train.set_role(featuretools_train.roles.unused_string, getml.data.roles.categorical)

featuretools_train

name     salary   lgID          teamIDCat     playerID      ...   SUM(pitchingpost.SHO)   SUM(pitchingpost.SO)
 role     target   categorical   categorical   categorical   ...               numerical              numerical
    0     870000   NL            ATL           barkele01     ...                       0                      0
    1     550000   NL            ATL           bedrost01     ...                       0                      2
    2     545000   NL            ATL           benedbr01     ...                       0                      0
    3     625000   NL            ATL           ceronri01     ...                       0                      0
    4     800000   NL            ATL           chambch01     ...                       0                      0
             ...   ...           ...           ...                                   ...                    ...
18567    4875000   NL            WAS           strasst01     ...                       0                      0
18568     750000   NL            WAS           tracych01     ...                       0                      0
18569    4000000   NL            WAS           wangch01      ...                       0                      7
18570   13571428   NL            WAS           werthja01     ...                       0                      0
18571   12000000   NL            WAS           zimmery01     ...                       0                      0

 name   SUM(pitchingpost.SV)   SUM(pitchingpost.W)   SUM(pitchingpost.WP)
 role              numerical             numerical              numerical
    0                      0                     0                      0
    1                      0                     0                      1
    2                      0                     0                      0
    3                      0                     0                      0
    4                      0                     0                      0
                         ...                   ...                    ...
18567                      0                     0                      0
18568                      0                     0                      0
18569                      0                     1                      0
18570                      0                     0                      0
18571                      0                     0                      0


18572 rows x 695 columns
memory usage: 97.24 MB
type: getml.DataFrame

In [63]:
featuretools_test.set_role("salary", getml.data.roles.target)
featuretools_test.set_role(featuretools_test.roles.unused_float, getml.data.roles.numerical)
featuretools_test.set_role(featuretools_test.roles.unused_string, getml.data.roles.categorical)

featuretools_test

name    salary   lgID          teamIDCat     playerID      ...   SUM(pitchingpost.SHO)   SUM(pitchingpost.SO)
role    target   categorical   categorical   categorical   ...               numerical              numerical
   0    633333   NL            ATL           campri01      ...                       0                      0
   1    150000   NL            ATL           dedmoje01     ...                       0                      0
   2   1500000   NL            ATL           hornebo01     ...                       0                      0
   3    512500   AL            BAL           dempsri01     ...                       0                      0
   4    560000   AL            BAL           martide01     ...                       0                      4
           ...   ...           ...           ...                                   ...                    ...
4534    512500   NL            WAS           desmoia01     ...                       0                      0
4535    506000   NL            WAS           espinda01     ...                       0                      0
4536   3000000   NL            WAS           gorzeto01     ...                       0                      0
4537    481000   NL            WAS           matthry01     ...                       0                      0
4538   2300000   NL            WAS           zimmejo02     ...                       0                      0

name   SUM(pitchingpost.SV)   SUM(pitchingpost.W)   SUM(pitchingpost.WP)
role              numerical             numerical              numerical
   0                      0                     0                      0
   1                      0                     0                      0
   2                      0                     0                      0
   3                      0                     0                      0
   4                      0                     0                      0
                        ...                   ...                    ...
4534                      0                     0                      0
4535                      0                     0                      0
4536                      0                     0                      0
4537                      0                     0                      0
4538                      0                     0                      0


4539 rows x 695 columns
memory usage: 23.77 MB
type: getml.DataFrame

We train an untuned XGBoostRegressor on top of featuretools' features, just like we have done for getML's features.

Since some of featuretools features are categorical, we allow the pipeline to include these features as well. Other features contain NaN values, which is why we also apply getML's Imputation preprocessor.

In [64]:
imputation = getml.preprocessors.Imputation()

predictor = getml.predictors.XGBoostRegressor(n_jobs=1)

pipe3 = getml.pipeline.Pipeline(
    tags=['featuretools'],
    preprocessors=[imputation],
    predictors=[predictor],
    include_categorical=True,
)

pipe3

Pipeline(data_model='population',
         feature_learners=[],
         feature_selectors=[],
         include_categorical=True,
         loss_function='SquareLoss',
         peripheral=[],
         predictors=['XGBoostRegressor'],
         preprocessors=['Imputation'],
         share_selected_features=0.5,
         tags=['featuretools'])

In [65]:
pipe3.fit(featuretools_train)

Checking data model...

  Staging... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:00--:--
  Preprocessing... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:0000:00
  Checking... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:0000:00


The pipeline check generated 1 issues labeled INFO and 14 issues labeled WARNING.

To see the issues in full, run .check() on the pipeline.

  Staging... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:0000:00
  Preprocessing... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:0000:00
  XGBoost: Training as predictor... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 01:03m • 00:0100:02


Trained pipeline.

Time taken: 0:01:03.761300.



Pipeline(data_model='population',
         feature_learners=[],
         feature_selectors=[],
         include_categorical=True,
         loss_function='SquareLoss',
         peripheral=[],
         predictors=['XGBoostRegressor'],
         preprocessors=['Imputation'],
         share_selected_features=0.5,
         tags=['featuretools'])

In [66]:
featuretools_score = pipe3.score(featuretools_test)
featuretools_score

  Staging... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:0001:03
  Preprocessing... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% • 00:0200:00


date time             set used             target            mae            rmse   rsquared
0   2024-09-03 15:18:59   featuretools_train   salary    716216.5012    1297813.3733     0.8115
1   2024-09-03 15:19:01   featuretools_test    salary    782064.7582    1435156.4642     0.7795

#### 2.6 Features

The most important features look as follows:

In [67]:
pipe1.features.to_sql()[pipe1.features.sort(by="importances")[0].name]

```sql
DROP TABLE IF EXISTS "FEATURE_1_29";

CREATE TABLE "FEATURE_1_29" AS
SELECT LAST( t2."gameid__mapping_1_target_1_avg", t2."year__1_000000_days" ) AS "feature_1_29",
       t1.rowid AS rownum
FROM "SALARIES__STAGING_TABLE_1" t1
INNER JOIN "ALLSTARFULL__STAGING_TABLE_2" t2
ON t1."playerid" = t2."playerid"
WHERE t2."year__1_000000_days" <= t1."year"
GROUP BY t1.rowid;
```

In [68]:
pipe2.features.to_sql()[pipe2.features.sort(by="importances")[0].name]

```sql
-- The size of the SQL code for FEATURE_1_1 is 138668 characters, which is greater than the size_threshold of 50000!
-- To display very long features like this anyway, increase the size_threshold or set the size_threshold to None.
DROP TABLE IF EXISTS "FEATURE_1_1";

CREATE TABLE "FEATURE_1_1";
```

#### 2.7 Productionization

It is possible to productionize the pipeline by transpiling the features into production-ready SQL code.

In [72]:
# Creates a folder named baseball_pipeline containing
# the SQL code.
pipe2.features.to_sql().save("baseball_pipeline")

In [73]:
# Creates a folder named baseball_pipeline_spark containing
# the SQL code.
pipe2.features.to_sql(dialect=getml.pipeline.dialect.spark_sql).save("baseball_pipeline_spark")

#### 2.8 Discussion

For a more convenient overview, we summarize our results into a table.

In [71]:
scores = [fastprop_score, relboost_score, featuretools_score]
pd.DataFrame(data={
    'Name': ['getML: FastProp', 'getML: Relboost', 'featuretools'],
    'R-squared': [f'{score.rsquared:.2%}' for score in scores],
    'RMSE': [f'{score.rmse:,.0f}' for score in scores],
    'MAE': [f'{score.mae:,.0f}' for score in scores]
})

Name R-squared       RMSE      MAE
0  getML: FastProp    78.86%  1,400,879  764,428
1  getML: Relboost    84.11%  1,214,581  664,778
2     featuretools    77.95%  1,435,156  782,065

As we can see, Relboost outperforms FastProp and both algorithms outperform featuretools according to all three measures.

### 3. Conclusion

We have demonstrated how statistical relational learning can be used for sabermetrics. We have also shown that getML outperforms featuretools on this dataset.

## References

Motl, Jan, and Oliver Schulte. "The CTU prague relational learning repository." arXiv preprint arXiv:1511.03086 (2015).